In [1]:
import os
os.environ['CUDA_DEVICE_ORDER'] = 'PCI_BUS_ID'
os.environ['CUDA_VISIBLE_DEVICES'] = '' 

In [108]:
import numpy as np
import cv2
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import skimage

from sklearn.metrics import mean_squared_error
from skimage import data, img_as_float
from skimage.restoration import denoise_nl_means
from skimage.measure import compare_ssim as ssim
from random import shuffle
import math
from keras.models import model_from_json, load_model
from keras.layers import *
from keras.models import Model
from keras import regularizers
from keras import backend as K
from keras.callbacks import TensorBoard, ReduceLROnPlateau, CSVLogger, EarlyStopping, ModelCheckpoint
from keras.layers.core import Lambda
import pickle
from random import randint
from utilities import *
%matplotlib inline


In [109]:
def rgb2gray(rgb):

    r, g, b = rgb[:,:,:,0], rgb[:,:,:,1], rgb[:,:,:,2]
    gray = 0.2989 * r + 0.5870 * g + 0.1140 * b

    return gray

def read_images_from_folder(folder_path):
    images = []
    for filename in os.listdir(folder_path):
        img = cv2.imread(os.path.join(folder_path,filename),0)
        if img is not None:
            images.append(img)
    return np.array(images)
        

In [4]:
raw_images = read_images_from_folder('./data/standard_test_images/gd/')

In [5]:
raw_512x512 = []
raw_256x256 = []
for img in raw_images:
    if img.shape == (512,512):
        raw_512x512.append(img)
    elif img.shape == (256,256):
        raw_256x256.append(img)

raw_512x512 = np.array(raw_512x512)
raw_256x256 = np.array(raw_256x256)
    

In [6]:
#Adding noise to images
def add_noise(images):
    
    noisy_set = []
    for image in images:
        print len(noisy_set)
        for noise_std in xrange(20,45,5):
            for proportion in xrange(2,8,2):
                noise = 0.25*proportion*np.random.normal(0,noise_std,image.shape)
                noisy_set.append((image,np.clip(noise + image,0.,255.)))
    shuffle(noisy_set)
    return np.array(noisy_set)
   
#Shuffle the noisy image ground truth pair to randomize the noise distribution in the dataset
def expand_pair(noisy_set):   
    ground_truth=[]
    noisy_images = []
    for i in range(noisy_set.shape[0]):
        ground_truth.append(noisy_set[i][0].reshape((noisy_set[i][0].shape[0],noisy_set[i][0].shape[1],1)))
        noisy_images.append(noisy_set[i][1].reshape((noisy_set[i][1].shape[0],noisy_set[i][1].shape[1],1)))
    return np.array(ground_truth), np.array(noisy_images)

In [7]:
noisy_set = add_noise(raw_512x512)
for i in range(noisy_set.shape[0]):
    cv2.imwrite("./data/standard_test_images/noise/image"+str(i)+".png",noisy_set[i][1])

0
15
30
45
60
75
90
105
120
135
150
165
180
195
210
225
240
255
270
285
300
315
330
345
360
375
390
405
420


In [8]:
#Shuffling and adding noise to the dataset
ground_truth,noisy_images = expand_pair(noisy_set)
print (ground_truth.shape, noisy_images.shape)

((435, 512, 512, 1), (435, 512, 512, 1))


In [9]:
#Split into training and cross validation and normalizing
train_size = int(ground_truth.shape[0]*0.8)
x_train = ground_truth[0:train_size]/255.
x_train_noisy = noisy_images[0:train_size]/255.
x_test = ground_truth[train_size:]/255.
x_test_noisy = noisy_images[train_size:]/255.
print (x_train_noisy.shape)
print (x_test_noisy.shape)

(348, 512, 512, 1)
(87, 512, 512, 1)


In [45]:
for i in range(ground_truth.shape[0]):
    cv2.imwrite("./data/cifar-bw/image"+str(i)+".png",ground_truth[i])
    
for i in range(noisy_images.shape[0]):
    cv2.imwrite("./data/noisy-cifar-bw/image"+str(i)+".png",noisy_images[i])

In [10]:
#lr_reducer = ReduceLROnPlateau(factor = np.sqrt(0.1), cooldown=0, patience=2, min_lr=0.5e-6)
#csv_logger = CSVLogger('./models/simple_cnn_autoencoder.csv')
#early_stopper = EarlyStopping(min_delta=0.001,patience=30)
model_checkpoint = ModelCheckpoint('./models/simple_cnn_autoencoder.hdf5',monitor = 'loss', verbose = 1,save_best_only=True)

In [11]:
x_train_noisy.shape

(348, 512, 512, 1)

In [12]:
#Defining the model

def get_simple_cnn_autoencoder_model(model_path=None):
    
    if(model_path is None):
        autoencoder = None
    else:
        autoencoder = read_model_json(model_path) 
    
    if(autoencoder is None):
        input_img = Input(shape=((None,None,1)))  # adapt this if using `channels_first` image data format

        x = Conv2D(64, (3, 3), activation='relu', padding='same')(input_img)
        x = MaxPooling2D((2, 2), padding='same')(x)
        x = Conv2D(64, (3, 3), activation='relu', padding='same')(x)
        encoded = MaxPooling2D((2, 2), padding='same')(x)

        x = Conv2D(64, (3, 3), activation='relu', padding='same')(encoded)
        x = UpSampling2D((2, 2))(x)
        x = Conv2D(64, (3, 3), activation='relu', padding='same')(x)
        x = UpSampling2D((2, 2))(x)
        decoded = Conv2D(1, (3, 3), activation='sigmoid', padding='same')(x)

        autoencoder = Model(input_img, decoded)
        autoencoder.compile(optimizer='sgd', loss='mean_squared_error',metrics = ['accuracy'])

    print (autoencoder.summary())
    return autoencoder

In [13]:
#Training the model
autoencoder = get_simple_cnn_autoencoder_model()


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, None, None, 1)     0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, None, None, 64)    640       
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, None, None, 64)    0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, None, None, 64)    36928     
_________________________________________________________________
max_pooling2d_2 (MaxPooling2 (None, None, None, 64)    0         
_________________________________________________________________
conv2d_3 (Conv2D)            (None, None, None, 64)    36928     
_________________________________________________________________
up_sampling2d_1 (UpSampling2 (None, None, None, 64)    0         
__________

In [14]:
autoencoder.fit(x_train_noisy, x_train,
                epochs=50,
                batch_size=5,
                shuffle=True,
                validation_data=(x_test_noisy, x_test),
                callbacks=[TensorBoard(log_dir='/tmp/autoencoder', histogram_freq=0, write_graph=True), model_checkpoint])

Train on 348 samples, validate on 87 samples
Epoch 1/50
348/348 [==============================] - 886s - loss: 0.0425 - acc: 2.8220e-04 - val_loss: 0.0400 - val_acc: 3.4385e-04
Epoch 2/50
348/348 [==============================] - 888s - loss: 0.0415 - acc: 3.4671e-04 - val_loss: 0.0392 - val_acc: 4.9196e-04
Epoch 3/50
348/348 [==============================] - 888s - loss: 0.0405 - acc: 3.9772e-04 - val_loss: 0.0382 - val_acc: 5.6580e-04
Epoch 4/50
348/348 [==============================] - 888s - loss: 0.0392 - acc: 4.3473e-04 - val_loss: 0.0370 - val_acc: 5.7273e-04
Epoch 5/50
348/348 [==============================] - 657s - loss: 0.0378 - acc: 4.9241e-04 - val_loss: 0.0356 - val_acc: 5.9167e-04
Epoch 6/50
348/348 [==============================] - 612s - loss: 0.0360 - acc: 5.5120e-04 - val_loss: 0.0338 - val_acc: 6.0943e-04
Epoch 7/50
348/348 [==============================] - 611s - loss: 0.0340 - acc: 5.9150e-04 - val_loss: 0.0318 - val_acc: 6.2491e-04
Epoch 8/50
348/348 [====

348/348 [==============================] - 619s - loss: 0.0059 - acc: 7.3113e-04 - val_loss: 0.0057 - val_acc: 6.7086e-04
Epoch 27/50
348/348 [==============================] - 618s - loss: 0.0058 - acc: 7.3364e-04 - val_loss: 0.0056 - val_acc: 6.7253e-04
Epoch 28/50
348/348 [==============================] - 618s - loss: 0.0057 - acc: 7.3605e-04 - val_loss: 0.0055 - val_acc: 6.7288e-04
Epoch 29/50
348/348 [==============================] - 618s - loss: 0.0057 - acc: 7.3769e-04 - val_loss: 0.0054 - val_acc: 6.7489e-04
Epoch 30/50
348/348 [==============================] - 618s - loss: 0.0056 - acc: 7.3926e-04 - val_loss: 0.0053 - val_acc: 6.7617e-04
Epoch 31/50
348/348 [==============================] - 618s - loss: 0.0055 - acc: 7.4050e-04 - val_loss: 0.0053 - val_acc: 6.7735e-04
Epoch 32/50
348/348 [==============================] - 620s - loss: 0.0055 - acc: 7.4229e-04 - val_loss: 0.0052 - val_acc: 6.7792e-04
Epoch 33/50
348/348 [==============================] - 618s - loss: 0.0054

In [110]:
#Function to get saved keras model
def read_model_json(jsonfilePath,h5filePath):
    try:
        json_file = open(jsonfilePath, 'r')
        print json_file
        loaded_model_json = json_file.read()
        json_file.close()
        print "hello"
        loaded_model = model_from_json(loaded_model_json)
         
        # load weights into new model
        loaded_model.load_weights(h5filePath)

        return loaded_model
    except:
        return None

In [113]:
def get_gated_connections(gatePercentageFactor,inputLayer):
    gateFactor = Input(tensor = K.variable([gatePercentageFactor]))
    fractionG = Lambda(lambda x: x[0]*x[1])([inputLayer,gateFactor])
    complement = Lambda(lambda x: x[0] - x[1])([inputLayer,fractionG])
    
    return gateFactor,fractionG,complement

#x is conv layer
#y is de-conv layer
#gf is gating factor
#fg is fractional input from gate
#c is complement ie remaining fraction from the gate
#jt joining tensor of convolution layer and previous de-conv layer 

def get_cnn_dsc_architecture(model_path=None):
    
    if(model_path is None):
        sym_autoencoder = None
    else:
        sym_autoencoder = read_model_json(model_path[0],model_path[1])
        print model_path[0],model_path[1]
    if(sym_autoencoder is None):
        input_img = Input(shape=(None,None,1), name = "Image_input")  # adapt this if using `channels_first` image data format
        x1 = Conv2D(64, (4, 4), activation='relu', padding='same')(input_img)
        gf1,fg1,c1 = get_gated_connections(0.1,x1)

        x = MaxPooling2D((2, 2), padding='same')(fg1)
        x2 = Conv2D(64, (4, 4), activation='relu', padding='same')(x) 
        gf2,fg2,c2 = get_gated_connections(0.2,x2)

        x = MaxPooling2D((2, 2), padding='same')(fg2)
        x3 = Conv2D(128, (4, 4), activation='relu', padding='same')(x) 
        gf3,fg3,c3 = get_gated_connections(0.3,x3)

        x = MaxPooling2D((2, 2), padding='same')(x3)
        x4 = Conv2D(256, (4, 4), activation='relu', padding='same')(x) 
        gf4,fg4,c4 = get_gated_connections(0.4,x4)

        x = MaxPooling2D((2, 2), padding='same')(x4)
        x5 = Conv2D(512, (4, 4), activation='relu', padding='same')(x) 

        x = UpSampling2D((2, 2))(x5)
        y1 = Conv2DTranspose(256, (4, 4), activation='relu', padding='same')(x) 
        jt4 = Add()([y1,c4])
        x = UpSampling2D((2, 2))(jt4)

        y2 = Conv2DTranspose(128, (4, 4), activation='relu', padding='same')(x) 
        jt3 = Add()([y2,c3])
        x = UpSampling2D((2, 2))(jt3)

        y3 = Conv2DTranspose(64, (4, 4), activation='relu', padding='same')(x) 
        jt2 = Add()([y3,c2])
        x = UpSampling2D((2, 2))(jt2)

        jt1 = Add()([x,c1])
        y4 = Conv2DTranspose(64, (4, 4), activation='relu', padding='same')(jt1)
        y5 = Conv2DTranspose(1, (4, 4), activation='relu', padding='same')(y4) 

        layers = y5

        sym_autoencoder = Model([input_img,gf1,gf2,gf3,gf4],layers)
        sym_autoencoder.compile(optimizer='sgd', loss = 'mean_squared_error', metrics = ['accuracy'])
        print "Model created"
    else:
        print "Saved model loaded"
    print sym_autoencoder.summary()
    return sym_autoencoder

In [114]:
sym_autoencoder = get_cnn_dsc_architecture()

Model created
____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
Image_input (InputLayer)         (None, None, None, 1) 0                                            
____________________________________________________________________________________________________
conv2d_7 (Conv2D)                (None, None, None, 64 1088        Image_input[0][0]                
____________________________________________________________________________________________________
input_2 (InputLayer)             (1,)                  0                                            
____________________________________________________________________________________________________
lambda_1 (Lambda)                (None, None, None, 64 0           conv2d_7[0][0]                   
                                                                   input_2[0]

In [115]:
model_checkpoint1 = ModelCheckpoint('./models/gated_cnn_autoencoder.hdf5',monitor = 'loss', verbose = 1,save_best_only=True)

In [116]:
sym_autoencoder.fit(x_train_noisy, x_train,
                epochs=50,
                batch_size=5,
                shuffle=True,
                validation_data=(x_test_noisy, x_test),
                callbacks=[TensorBoard(log_dir='/tmp/gated_cnn_autoencoder', 
                                       histogram_freq=0,
                                       write_graph=True),model_checkpoint1])

Train on 348 samples, validate on 87 samples
Epoch 1/50
 10/348 [..............................] - ETA: 1319s - loss: 0.3233 - acc: 3.8910e-05

KeyboardInterrupt: 

In [21]:
#getting testing images

In [127]:
#Denoising using CNN symmetric Autoencoders
out_sym_autoencoder = sym_autoencoder.predict(x_train_noisy[0:1],verbose=1)
print (out_sym_autoencoder.shape)

1/1 [==============================] - 0s
(1, 64, 64, 1)


In [105]:
test = cv2.imread("data/standard_test_images/noise/image21.png",0)
test = np.array(test)
test = test.reshape(1,test.shape[0],test.shape[1],1)
test =  test/255.0
test

array([[[[ 0.59215686],
         [ 0.6       ],
         [ 0.68235294],
         ..., 
         [ 0.5372549 ],
         [ 0.56078431],
         [ 0.4745098 ]],

        [[ 0.76862745],
         [ 0.76078431],
         [ 0.52941176],
         ..., 
         [ 0.76862745],
         [ 0.57254902],
         [ 0.59215686]],

        [[ 0.68235294],
         [ 0.54117647],
         [ 0.57254902],
         ..., 
         [ 0.48235294],
         [ 0.65490196],
         [ 0.5372549 ]],

        ..., 
        [[ 0.49803922],
         [ 0.45490196],
         [ 0.4745098 ],
         ..., 
         [ 0.49019608],
         [ 0.36862745],
         [ 0.39607843]],

        [[ 0.5254902 ],
         [ 0.43137255],
         [ 0.51764706],
         ..., 
         [ 0.4627451 ],
         [ 0.5372549 ],
         [ 0.34509804]],

        [[ 0.62352941],
         [ 0.6       ],
         [ 0.56470588],
         ..., 
         [ 0.41176471],
         [ 0.4627451 ],
         [ 0.49411765]]]])

In [106]:
#Denoising using Autoencoders
out_autoencoder = autoencoder.predict(test,verbose=1).astype('float64')
print (out_autoencoder[0].shape)

1/1 [==============================] - 0s
(512, 512, 1)


In [107]:
#plt.imshow(out_autoencoder[0])
cv2.imwrite("test.png",(out_autoencoder[0]*255))
test =test*255
test



array([[[[ 151.],
         [ 153.],
         [ 174.],
         ..., 
         [ 137.],
         [ 143.],
         [ 121.]],

        [[ 196.],
         [ 194.],
         [ 135.],
         ..., 
         [ 196.],
         [ 146.],
         [ 151.]],

        [[ 174.],
         [ 138.],
         [ 146.],
         ..., 
         [ 123.],
         [ 167.],
         [ 137.]],

        ..., 
        [[ 127.],
         [ 116.],
         [ 121.],
         ..., 
         [ 125.],
         [  94.],
         [ 101.]],

        [[ 134.],
         [ 110.],
         [ 132.],
         ..., 
         [ 118.],
         [ 137.],
         [  88.]],

        [[ 159.],
         [ 153.],
         [ 144.],
         ..., 
         [ 105.],
         [ 118.],
         [ 126.]]]])

In [119]:
for i in range(100):
    cv2.imwrite("./data/denoise-cifar-bw/"+str(i)+".png",out_autoencoder[i]*255.)

In [57]:
from sklearn.metrics import mean_squared_error
from skimage.measure import compare_psnr,compare_mse
def get_psnr(imageA,imageB):
    maxI = 1.0
    try:
        return 20*math.log10(maxI) - 10*math.log10(compare_mse(imageA.flatten(),imageB.flatten()))
    except:
        return 20*math.log10(maxI)

def get_psnr_result(x_test, out):
    psnr_sum = 0
    for i in range(out.shape[0]):
        psnr_sum += compare_psnr(x_test[i].reshape(32,32,1),out[i].reshape(32,32,1),data_range=255)
        
    return 1.0*psnr_sum/out.shape[0];

def get_ssim_result(originalSet,noisySet):
    ssim_sum = 0
    originalSet = originalSet.reshape(originalSet.shape[0],32,32,1)
    noisySet = noisySet.reshape(noisySet.shape[0],32,32,1)
    for i in range(originalSet.shape[0]):
        ssim_sum += ssim(originalSet[i], noisySet[i],data_range=originalSet[i].max() - noisySet[i].min(), multichannel=True)
    return 1.0*ssim_sum/originalSet.shape[0]

In [165]:
def bm3d_denoise(noisy_image):
    noisy_image = noisy_image.reshape(noisy_image.shape[0],32,32)
    denoised = []
    count = 1
    for i in range(noisy_image.shape[0]):
        Basic_img = bm3d.BM3D_1st_step(noisy_image[i])
        Final_img = bm3d.BM3D_2nd_step(Basic_img, noisy_image[i])
        denoised.append(Final_img)
        if (count%10 == 0):
            print (str(count)+ "images denoised")
        count+=1
        
    return np.array(denoised)

def nlm_denoise(noisy_image):
    noisy_image = noisy_image.reshape(noisy_image.shape[0],32,32,1)
    denoised = []
    count = 1
    
    for image in noisy_image:
        denoised_image = denoise_nl_means(image, 7, 11, 0.5,multichannel = False)
        denoised.append(denoised_image)
        if(count%100 == 0) :
            print(str(count)+" images denoised")
        count+=1
    return np.array(denoised)

In [134]:
print (test_images.shape,out_autoencoder.shape)
print (compare_mse(test_images[0].flatten(),(out_autoencoder[0]*255.).flatten()))
get_psnr_result(out_autoencoder*255.,test_images)

((10000, 32, 32, 1), (10000, 32, 32, 1))
458.092258419


22.066576979897317

In [39]:
print (test_images.shape,out_sym_autoencoder.shape)
print (mean_squared_error(test_images[0].flatten(),out_sym_autoencoder[0].flatten()))
get_psnr_result(out_sym_autoencoder,test_images)

NameError: name 'out_sym_autoencoder' is not defined

In [39]:
import bm3d

In [40]:
noisy_test_images.shape
bm3d_out = bm3d_denoise(noisy_test_images)

error: /home/travis/miniconda/conda-bld/work/opencv-2.4.11/modules/core/src/dxt.cpp:2330: error: (-213) Odd-size DCT's are not implemented in function dct


In [ ]:
bm3d_out_norm = bm3d_out.astype('float64')/255.0

In [ ]:
get_psnr_result(bm3d_out_norm,test_images)

In [166]:
print(noisy_test_images.shape)
nlm_out = nlm_denoise(noisy_test_images*255.)
nlm_out = nlm_out.astype('float64')

(10000, 32, 32, 1)


KeyboardInterrupt: 

In [157]:
print nlm_out.shape,test_images.shape
get_psnr_result(nlm_out,test_images)

(10000, 32, 32) (10000, 32, 32, 1)


18.414818545893922

In [136]:
get_ssim_result(test_images,out_autoencoder*255.)

0.69608629344603479

In [66]:
get_ssim_result(test_images,out_sym_autoencoder)

0.718734871276698

In [ ]:
get_ssim_result(test_images,bm3d_out_norm)

In [69]:
get_ssim_result(test_images,nlm_out)

0.49438484841716263

In [114]:
model = load_model("./models/gated_cnn_autoencoder.hdf5")

In [151]:
model = autoencoder

In [21]:
bwmodel= model.predict(noisy_test_images,verbose=1)

10000/10000 [==============================] - 7s     


In [24]:
print (test_images.shape,bwmodel.shape)
get_psnr_result(bwmodel,test_images)

((10000, 32, 32, 1), (10000, 32, 32, 1))


16.773690910050014

In [129]:
def read_images_from_folder(folder_path):
    images = []
    for filename in os.listdir(folder_path):
        img = cv2.imread(os.path.join(folder_path,filename),0)
        if img is not None:
            images.append((img,filename))
    return np.array(images)
        

In [130]:
standard_test_images = read_images_from_folder('./data/standard_test_images/gd/')

In [131]:
standard_test_images.shape

(60, 2)

In [132]:
standard_test_images[0]

array([ array([[ 90,  95, 100, ..., 113, 115, 110],
       [ 96, 107, 110, ..., 111, 118, 111],
       [103, 100, 115, ...,  99, 111, 113],
       ..., 
       [111, 116, 123, ..., 130, 141, 131],
       [106, 103, 119, ..., 133, 141, 137],
       [128, 121, 128, ..., 128, 143, 137]], dtype=uint8),
       'tank2.tiff'], dtype=object)

In [133]:
std_test_images = []
image_names = []
for img in standard_test_images:
    std_test_images.append(img[0])
    image_names.append(img[1])
std_test_images = np.array(std_test_images)

In [134]:
noisy_std_test_images = add_noise(std_test_images)

In [135]:
for index in range(noisy_std_test_images.shape[0]):
    cv2.imwrite('./data/standard_test_images/noise/'+image_names[index],noisy_std_test_images[index])

In [152]:
def denoise_by_patches(noisy_image,model,stride):
    sizeX = noisy_image.shape[0]
    sizeY = noisy_image.shape[1]
    
    denoise_image = np.zeros((sizeX,sizeY), np.int64)
    overlap_mat = np.zeros((sizeX,sizeY), np.int64)
    norm_image = noisy_image/255.
    cnt = 1
    for row in xrange(0,sizeX - 64,stride):
        for col in xrange(0,sizeY - 64,stride):
            #print cnt
            cnt+=1
            patch = norm_image[row:row+64,col:col+64]
            #print patch.shape
            de_patch = [patch]
            de_patch = np.array(de_patch)
            de_patch = np.reshape(de_patch, (1,64,64,1))
            #print de_patch.shape
            de_patch = model.predict(de_patch)
            de_patch = de_patch[0]*255.
            de_patch = np.reshape(de_patch, (64,64)).astype('int64')
            print row,col,denoise_image[row:row+64,col:col+64].shape, de_patch.shape
            denoise_image[row:row+64 ,col:col+64] = denoise_image[row:row+64 ,col:col+64] + de_patch
            overlap_mat[row:row+64 ,col:col+64] = overlap_mat[row:row+64 ,col:col+64] + 1
            #print overlap_mat
            
    
    print overlap_mat
    for row in xrange(0,sizeX):
        for col in xrange(0,sizeY):
            if(overlap_mat[row][col]!=0):
                denoise_image[row][col] = denoise_image[row][col]/(overlap_mat[row][col]*1.0)
            else:
                denoise_image[row][col] = denoise_image[row][col]//2.0
    return denoise_image


In [153]:
de_cam = denoise_by_patches(noisy_std_test_images[8],model,1)
cv2.imwrite('./data/standard_test_images/denoise/cameraman.tif',de_cam)

0 0 (64, 64) (64, 64)
0 1 (64, 64) (64, 64)
0 2 (64, 64) (64, 64)
0 3 (64, 64) (64, 64)
0 4 (64, 64) (64, 64)
0 5 (64, 64) (64, 64)
0 6 (64, 64) (64, 64)
0 7 (64, 64) (64, 64)
0 8 (64, 64) (64, 64)
0 9 (64, 64) (64, 64)
0 10 (64, 64) (64, 64)
0 11 (64, 64) (64, 64)
0 12 (64, 64) (64, 64)
0 13 (64, 64) (64, 64)
0 14 (64, 64) (64, 64)
0 15 (64, 64) (64, 64)
0 16 (64, 64) (64, 64)
0 17 (64, 64) (64, 64)
0 18 (64, 64) (64, 64)
0 19 (64, 64) (64, 64)
0 20 (64, 64) (64, 64)
0 21 (64, 64) (64, 64)
0 22 (64, 64) (64, 64)
0 23 (64, 64) (64, 64)
0 24 (64, 64) (64, 64)
0 25 (64, 64) (64, 64)
0 26 (64, 64) (64, 64)
0 27 (64, 64) (64, 64)
0 28 (64, 64) (64, 64)
0 29 (64, 64) (64, 64)
0 30 (64, 64) (64, 64)
0 31 (64, 64) (64, 64)
0 32 (64, 64) (64, 64)
0 33 (64, 64) (64, 64)
0 34 (64, 64) (64, 64)
0 35 (64, 64) (64, 64)
0 36 (64, 64) (64, 64)
0 37 (64, 64) (64, 64)
0 38 (64, 64) (64, 64)
0 39 (64, 64) (64, 64)
0 40 (64, 64) (64, 64)
0 41 (64, 64) (64, 64)
0 42 (64, 64) (64, 64)
0 43 (64, 64) (64, 64

0 385 (64, 64) (64, 64)
0 386 (64, 64) (64, 64)
0 387 (64, 64) (64, 64)
0 388 (64, 64) (64, 64)
0 389 (64, 64) (64, 64)
0 390 (64, 64) (64, 64)
0 391 (64, 64) (64, 64)
0 392 (64, 64) (64, 64)
0 393 (64, 64) (64, 64)
0 394 (64, 64) (64, 64)
0 395 (64, 64) (64, 64)
0 396 (64, 64) (64, 64)
0 397 (64, 64) (64, 64)
0 398 (64, 64) (64, 64)
0 399 (64, 64) (64, 64)
0 400 (64, 64) (64, 64)
0 401 (64, 64) (64, 64)
0 402 (64, 64) (64, 64)
0 403 (64, 64) (64, 64)
0 404 (64, 64) (64, 64)
0 405 (64, 64) (64, 64)
0 406 (64, 64) (64, 64)
0 407 (64, 64) (64, 64)
0 408 (64, 64) (64, 64)
0 409 (64, 64) (64, 64)
0 410 (64, 64) (64, 64)
0 411 (64, 64) (64, 64)
0 412 (64, 64) (64, 64)
0 413 (64, 64) (64, 64)
0 414 (64, 64) (64, 64)
0 415 (64, 64) (64, 64)
0 416 (64, 64) (64, 64)
0 417 (64, 64) (64, 64)
0 418 (64, 64) (64, 64)
0 419 (64, 64) (64, 64)
0 420 (64, 64) (64, 64)
0 421 (64, 64) (64, 64)
0 422 (64, 64) (64, 64)
0 423 (64, 64) (64, 64)
0 424 (64, 64) (64, 64)
0 425 (64, 64) (64, 64)
0 426 (64, 64) (

1 315 (64, 64) (64, 64)
1 316 (64, 64) (64, 64)
1 317 (64, 64) (64, 64)
1 318 (64, 64) (64, 64)
1 319 (64, 64) (64, 64)
1 320 (64, 64) (64, 64)
1 321 (64, 64) (64, 64)
1 322 (64, 64) (64, 64)
1 323 (64, 64) (64, 64)
1 324 (64, 64) (64, 64)
1 325 (64, 64) (64, 64)
1 326 (64, 64) (64, 64)
1 327 (64, 64) (64, 64)
1 328 (64, 64) (64, 64)
1 329 (64, 64) (64, 64)
1 330 (64, 64) (64, 64)
1 331 (64, 64) (64, 64)
1 332 (64, 64) (64, 64)
1 333 (64, 64) (64, 64)
1 334 (64, 64) (64, 64)
1 335 (64, 64) (64, 64)
1 336 (64, 64) (64, 64)
1 337 (64, 64) (64, 64)
1 338 (64, 64) (64, 64)
1 339 (64, 64) (64, 64)
1 340 (64, 64) (64, 64)
1 341 (64, 64) (64, 64)
1 342 (64, 64) (64, 64)
1 343 (64, 64) (64, 64)
1 344 (64, 64) (64, 64)
1 345 (64, 64) (64, 64)
1 346 (64, 64) (64, 64)
1 347 (64, 64) (64, 64)
1 348 (64, 64) (64, 64)
1 349 (64, 64) (64, 64)
1 350 (64, 64) (64, 64)
1 351 (64, 64) (64, 64)
1 352 (64, 64) (64, 64)
1 353 (64, 64) (64, 64)
1 354 (64, 64) (64, 64)
1 355 (64, 64) (64, 64)
1 356 (64, 64) (

2 228 (64, 64) (64, 64)
2 229 (64, 64) (64, 64)
2 230 (64, 64) (64, 64)
2 231 (64, 64) (64, 64)
2 232 (64, 64) (64, 64)
2 233 (64, 64) (64, 64)
2 234 (64, 64) (64, 64)
2 235 (64, 64) (64, 64)
2 236 (64, 64) (64, 64)
2 237 (64, 64) (64, 64)
2 238 (64, 64) (64, 64)
2 239 (64, 64) (64, 64)
2 240 (64, 64) (64, 64)
2 241 (64, 64) (64, 64)
2 242 (64, 64) (64, 64)
2 243 (64, 64) (64, 64)
2 244 (64, 64) (64, 64)
2 245 (64, 64) (64, 64)
2 246 (64, 64) (64, 64)
2 247 (64, 64) (64, 64)
2 248 (64, 64) (64, 64)
2 249 (64, 64) (64, 64)
2 250 (64, 64) (64, 64)
2 251 (64, 64) (64, 64)
2 252 (64, 64) (64, 64)
2 253 (64, 64) (64, 64)
2 254 (64, 64) (64, 64)
2 255 (64, 64) (64, 64)
2 256 (64, 64) (64, 64)
2 257 (64, 64) (64, 64)
2 258 (64, 64) (64, 64)
2 259 (64, 64) (64, 64)
2 260 (64, 64) (64, 64)
2 261 (64, 64) (64, 64)
2 262 (64, 64) (64, 64)
2 263 (64, 64) (64, 64)
2 264 (64, 64) (64, 64)
2 265 (64, 64) (64, 64)
2 266 (64, 64) (64, 64)
2 267 (64, 64) (64, 64)
2 268 (64, 64) (64, 64)
2 269 (64, 64) (

3 141 (64, 64) (64, 64)
3 142 (64, 64) (64, 64)
3 143 (64, 64) (64, 64)
3 144 (64, 64) (64, 64)
3 145 (64, 64) (64, 64)
3 146 (64, 64) (64, 64)
3 147 (64, 64) (64, 64)
3 148 (64, 64) (64, 64)
3 149 (64, 64) (64, 64)
3 150 (64, 64) (64, 64)
3 151 (64, 64) (64, 64)
3 152 (64, 64) (64, 64)
3 153 (64, 64) (64, 64)
3 154 (64, 64) (64, 64)
3 155 (64, 64) (64, 64)
3 156 (64, 64) (64, 64)
3 157 (64, 64) (64, 64)
3 158 (64, 64) (64, 64)
3 159 (64, 64) (64, 64)
3 160 (64, 64) (64, 64)
3 161 (64, 64) (64, 64)
3 162 (64, 64) (64, 64)
3 163 (64, 64) (64, 64)
3 164 (64, 64) (64, 64)
3 165 (64, 64) (64, 64)
3 166 (64, 64) (64, 64)
3 167 (64, 64) (64, 64)
3 168 (64, 64) (64, 64)
3 169 (64, 64) (64, 64)
3 170 (64, 64) (64, 64)
3 171 (64, 64) (64, 64)
3 172 (64, 64) (64, 64)
3 173 (64, 64) (64, 64)
3 174 (64, 64) (64, 64)
3 175 (64, 64) (64, 64)
3 176 (64, 64) (64, 64)
3 177 (64, 64) (64, 64)
3 178 (64, 64) (64, 64)
3 179 (64, 64) (64, 64)
3 180 (64, 64) (64, 64)
3 181 (64, 64) (64, 64)
3 182 (64, 64) (

...

445 200 (64, 64) (64, 64)
445 201 (64, 64) (64, 64)
445 202 (64, 64) (64, 64)
445 203 (64, 64) (64, 64)
445 204 (64, 64) (64, 64)
445 205 (64, 64) (64, 64)
445 206 (64, 64) (64, 64)
445 207 (64, 64) (64, 64)
445 208 (64, 64) (64, 64)
445 209 (64, 64) (64, 64)
445 210 (64, 64) (64, 64)
445 211 (64, 64) (64, 64)
445 212 (64, 64) (64, 64)
445 213 (64, 64) (64, 64)
445 214 (64, 64) (64, 64)
445 215 (64, 64) (64, 64)
445 216 (64, 64) (64, 64)
445 217 (64, 64) (64, 64)
445 218 (64, 64) (64, 64)
445 219 (64, 64) (64, 64)
445 220 (64, 64) (64, 64)
445 221 (64, 64) (64, 64)
445 222 (64, 64) (64, 64)
445 223 (64, 64) (64, 64)
445 224 (64, 64) (64, 64)
445 225 (64, 64) (64, 64)
445 226 (64, 64) (64, 64)
445 227 (64, 64) (64, 64)
445 228 (64, 64) (64, 64)
445 229 (64, 64) (64, 64)
445 230 (64, 64) (64, 64)
445 231 (64, 64) (64, 64)
445 232 (64, 64) (64, 64)
445 233 (64, 64) (64, 64)
445 234 (64, 64) (64, 64)
445 235 (64, 64) (64, 64)
445 236 (64, 64) (64, 64)
445 237 (64, 64) (64, 64)
445 238 (64,

446 114 (64, 64) (64, 64)
446 115 (64, 64) (64, 64)
446 116 (64, 64) (64, 64)
446 117 (64, 64) (64, 64)
446 118 (64, 64) (64, 64)
446 119 (64, 64) (64, 64)
446 120 (64, 64) (64, 64)
446 121 (64, 64) (64, 64)
446 122 (64, 64) (64, 64)
446 123 (64, 64) (64, 64)
446 124 (64, 64) (64, 64)
446 125 (64, 64) (64, 64)
446 126 (64, 64) (64, 64)
446 127 (64, 64) (64, 64)
446 128 (64, 64) (64, 64)
446 129 (64, 64) (64, 64)
446 130 (64, 64) (64, 64)
446 131 (64, 64) (64, 64)
446 132 (64, 64) (64, 64)
446 133 (64, 64) (64, 64)
446 134 (64, 64) (64, 64)
446 135 (64, 64) (64, 64)
446 136 (64, 64) (64, 64)
446 137 (64, 64) (64, 64)
446 138 (64, 64) (64, 64)
446 139 (64, 64) (64, 64)
446 140 (64, 64) (64, 64)
446 141 (64, 64) (64, 64)
446 142 (64, 64) (64, 64)
446 143 (64, 64) (64, 64)
446 144 (64, 64) (64, 64)
446 145 (64, 64) (64, 64)
446 146 (64, 64) (64, 64)
446 147 (64, 64) (64, 64)
446 148 (64, 64) (64, 64)
446 149 (64, 64) (64, 64)
446 150 (64, 64) (64, 64)
446 151 (64, 64) (64, 64)
446 152 (64,

447 23 (64, 64) (64, 64)
447 24 (64, 64) (64, 64)
447 25 (64, 64) (64, 64)
447 26 (64, 64) (64, 64)
447 27 (64, 64) (64, 64)
447 28 (64, 64) (64, 64)
447 29 (64, 64) (64, 64)
447 30 (64, 64) (64, 64)
447 31 (64, 64) (64, 64)
447 32 (64, 64) (64, 64)
447 33 (64, 64) (64, 64)
447 34 (64, 64) (64, 64)
447 35 (64, 64) (64, 64)
447 36 (64, 64) (64, 64)
447 37 (64, 64) (64, 64)
447 38 (64, 64) (64, 64)
447 39 (64, 64) (64, 64)
447 40 (64, 64) (64, 64)
447 41 (64, 64) (64, 64)
447 42 (64, 64) (64, 64)
447 43 (64, 64) (64, 64)
447 44 (64, 64) (64, 64)
447 45 (64, 64) (64, 64)
447 46 (64, 64) (64, 64)
447 47 (64, 64) (64, 64)
447 48 (64, 64) (64, 64)
447 49 (64, 64) (64, 64)
447 50 (64, 64) (64, 64)
447 51 (64, 64) (64, 64)
447 52 (64, 64) (64, 64)
447 53 (64, 64) (64, 64)
447 54 (64, 64) (64, 64)
447 55 (64, 64) (64, 64)
447 56 (64, 64) (64, 64)
447 57 (64, 64) (64, 64)
447 58 (64, 64) (64, 64)
447 59 (64, 64) (64, 64)
447 60 (64, 64) (64, 64)
447 61 (64, 64) (64, 64)
447 62 (64, 64) (64, 64)


447 382 (64, 64) (64, 64)
447 383 (64, 64) (64, 64)
447 384 (64, 64) (64, 64)
447 385 (64, 64) (64, 64)
447 386 (64, 64) (64, 64)
447 387 (64, 64) (64, 64)
447 388 (64, 64) (64, 64)
447 389 (64, 64) (64, 64)
447 390 (64, 64) (64, 64)
447 391 (64, 64) (64, 64)
447 392 (64, 64) (64, 64)
447 393 (64, 64) (64, 64)
447 394 (64, 64) (64, 64)
447 395 (64, 64) (64, 64)
447 396 (64, 64) (64, 64)
447 397 (64, 64) (64, 64)
447 398 (64, 64) (64, 64)
447 399 (64, 64) (64, 64)
447 400 (64, 64) (64, 64)
447 401 (64, 64) (64, 64)
447 402 (64, 64) (64, 64)
447 403 (64, 64) (64, 64)
447 404 (64, 64) (64, 64)
447 405 (64, 64) (64, 64)
447 406 (64, 64) (64, 64)
447 407 (64, 64) (64, 64)
447 408 (64, 64) (64, 64)
447 409 (64, 64) (64, 64)
447 410 (64, 64) (64, 64)
447 411 (64, 64) (64, 64)
447 412 (64, 64) (64, 64)
447 413 (64, 64) (64, 64)
447 414 (64, 64) (64, 64)
447 415 (64, 64) (64, 64)
447 416 (64, 64) (64, 64)
447 417 (64, 64) (64, 64)
447 418 (64, 64) (64, 64)
447 419 (64, 64) (64, 64)
447 420 (64,

True

In [116]:
def denoise_std_test_images(images,model,stride):
    denoised_images = []
    for index in range(images.shape[0]):
        d_image = denoise_by_patches(images[index],model,stride)
        denoised_images.append(d_image)
        cv2.imwrite('./data/standard_test_images/denoise/'+image_names[index],d_image)
        print compare_psnr(d_image.astype('uint8'),std_test_images[index].astype('uint8'),data_range=255)
        print "image " + str(index)+ " denoised"

In [138]:
image_names[8]

'cameraman.tif'

In [117]:
denoise_std_test_images(noisy_std_test_images,model,1)

(512, 512)
512 512


ValueError: The model expects 5  arrays, but only received one array. Found: array with shape (1, 64, 64, 1)

In [196]:
nlm_camera = cv2.fastNlMeansDenoising(noisy_std_test_images[0].astype('uint8'),None,25,7 ,21)
cv2.imwrite("nlm.png",nlm_camera)
print compare_psnr(nlm_camera,std_test_images[0])

30.1276904426


In [53]:
print noisy_std_test_images[0][448:448+64,0:0+64].shape

(64, 64)


In [48]:
# your code goes here
from queue import Queue
from threading import Thread

class DaemonWorker(Thread):
   def __init__(self, queue):
       Thread.__init__(self)
       self.queue = queue

   def run(self):
       while True:
           list_of_pixels = self.queue.get()
           # Do your operation here.
           self.queue.task_done()
           
def run():
	# assuming image 484x484
	# serialize image such that you get 1x484 and 484 such rows. 
	# i.e Each element at an index, is the list of pixels in a row.
	queue = Queue()
	for x in xrange(number_of_threads):
		worker = DaemonWorker(queue)
		worker.daemon = True
		worker.start()
	for row_in_pic in image:
		queue.put(row_in_pic)

ImportError: No module named queue

In [65]:
a = np.ones((63,64),np.uint8)
print a.shape

(63, 64)


In [66]:
b = np.resize(a,(64,64))
print b.shape

(64, 64)
